In [229]:
import numpy as np
import pyproj
import matplotlib.pyplot as plt
%config InlineBackend.figure_format = 'svg'
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot 
import plotly.animation as animation
init_notebook_mode(connected=True)
import pandas as pd
import netCDF4
from PIL import Image
import os
from src.utils.constants import *


In [263]:
def plot_groundtrack(Sat_ID, Coords, res=(800, 800), Mode='markers+lines', style='seaborn', 
                     marker_size=0.5, tracecolor='red', play_duration=300): 
    Lat = Coords[:, 0]
    Lon = Coords[:, 1]

    # converting latitude and longitude to equirectangular projection
    #Lat_equi = 800 *  np.cos(np.deg2rad(Lat)) * np.cos(np.deg2rad(Lon))
    #Lon_equi = -400 * np.cos(np.deg2rad(Lat)) * np.sin(np.deg2rad(Lon))
    Lat_equi = 800 *  np.cos(Lat) * np.cos(Lon)
    Lon_equi = -400 * np.cos(Lat) * np.sin(Lon)


    animation_steps = 40
    
    fig = make_subplots(rows=1, cols=2, subplot_titles=("Orthographic Projection", "Flat Projection"), specs=[[{"type": "geo"}, {"type": "geo"}]], 
                    print_grid=True)

    fig.add_trace(go.Scattergeo(lat=Lat, lon=Lon, mode=Mode, marker=dict(size=marker_size, color=tracecolor), name=Sat_ID), row=1, col=1)
    fig.add_trace(go.Scattergeo(lat=Lat_equi, lon=Lon_equi, mode=Mode, marker=dict(size=marker_size, color=tracecolor), showlegend=False), row=1, col=2)

    fig.update_geos(projection_type="orthographic", row=1, col=1, 
                    showland=True, landcolor="LightGreen", showocean=True, oceancolor="#179fff", showlakes=True, lakecolor="#179fff", 
                    showrivers=True, rivercolor="#179fff")
    fig.update_geos(projection_type="equirectangular", row=1, col=2, 
                    showland=True, landcolor="LightGreen", showocean=True, oceancolor="#179fff", showlakes=True, lakecolor="#179fff", 
                    showrivers=True, rivercolor="#179fff")
    fig.update_layout(template=style, width=res[0], height=res[1]//2, title_text="Groundtrack", showlegend=True)

    frames = []
    for i in range(1, animation_steps + 1):
        alpha = i / animation_steps
        frames.append(go.Frame(data=[go.Scattergeo(lat=Lat[:int(alpha*len(Lat))], lon=Lon[:int(alpha*len(Lon))],
                                                    mode=Mode, marker=dict(size=marker_size, color=tracecolor),
                                                    name=Sat_ID)],
                               layout=dict(geo=dict(projection_type='orthographic'))))

    fig.frames = frames
    fig.update_layout(updatemenus=[dict(type='buttons', showactive=False, buttons=[dict(label='Play',
                                                                                      method='animate',
                                                                                      args=[None, dict(frame=dict(duration=play_duration),
                                                                                                        fromcurrent=True,
                                                                                                        mode="immediate",
                                                                                                        transition=dict(duration=0))]),
                                                                                     dict(label='Pause',
                                                                                          method='animate',
                                                                                          args=[[None], dict(frame=dict(duration=0),
                                                                                                              mode='immediate',
                                                                                                              transition=dict(duration=0))])])])
    fig.show()

In [264]:
N = 200
#lat = np.linspace(0, 360, N)
#lon = np.linspace(0, 360, N)
lat = np.linspace(-180, 180, N)
lon = np.linspace(-180, 180, N)
c = np.array([lat, lon]).T

plot_groundtrack('Wal Ter', c, res=(1000, 1000), Mode='markers+lines', marker_size=0.8, style='seaborn', play_duration=50)


This is the format of your plot grid:
[ (1,1) geo  ]  [ (1,2) geo2 ]



In [ ]:
# create the Earth surface using a sphere meshgrid
theta, phi = np.linspace(0, 2 * np.pi, 50), np.linspace(0, np.pi, 50)
theta_grid, phi_grid = np.meshgrid(theta, phi)
x = np.sin(phi_grid) * np.cos(theta_grid)
y = np.sin(phi_grid) * np.sin(theta_grid)
z = np.cos(phi_grid)

# create a diffuse map of the Earth
img = Image.open('external_data/earth-albedo.jpg')
img = img.resize((360, 180))
albedo = np.array(img)

# create trace for the Earth surface
earth = go.Surface(x=x, y=y, z=z, opacity=1.0, surfacecolor=albedo, showscale=False)

# define orbit coordinates as a function of time
t = np.linspace(0, 10 * np.pi, 500)
x_orbit = np.cos(t)
y_orbit = np.sin(t)
z_orbit = np.zeros_like(t)

# create trace for the orbit
orbit = go.Scatter3d(x=x_orbit, y=y_orbit, z=z_orbit, mode='lines', line=dict(color='red', width=3))

# create a 3D plot with the Earth at the center and the orbit plotted around it
fig = go.Figure(data=[earth, orbit], layout=go.Layout(
    scene=dict(xaxis=dict(range=[-1, 1]), yaxis=dict(range=[-1, 1]), zaxis=dict(range=[-1, 1])),
    width=700, height=700, showlegend=False, margin=dict(l=0, r=0, b=0, t=0))
)

fig.show()